In [3]:
# Import packages.
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow import keras
from keras import layers
from keras import models
from keras.layers import LSTM, Dense
import matplotlib
from matplotlib import pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_squared_error
from math import sqrt
from numpy import concatenate
from tensorflow.keras import layers
from tensorflow.keras.layers import Input, Dense, Conv3D, MaxPooling3D, UpSampling3D, Conv3DTranspose
from tensorflow.keras.models import Model

In [2]:
# Read dataset.
df = pd.read_csv("df_subset.csv")
# Drop unneeded columns caused by merging.
df = df[df.columns.drop(list(df.filter(regex='Unnamed')))]
# Add calculated fields.
df["wind_speed"] = np.sqrt(df["u"]**2 + df["v"]**2)
df["wind_dir"] = np.sqrt(df["u"]**2 + df["v"]**2)

In [4]:
df["time"]

0           2018-01-01 00:00:00
1           2018-01-01 00:00:00
2           2018-01-01 00:00:00
3           2018-01-01 00:00:00
4           2018-01-01 00:00:00
                   ...         
19808251    2018-01-31 23:00:00
19808252    2018-01-31 23:00:00
19808253    2018-01-31 23:00:00
19808254    2018-01-31 23:00:00
19808255    2018-01-31 23:00:00
Name: time, Length: 19808256, dtype: object

In [5]:
# Subset to a specific point.
df_subset = df[df["time"] <= '2018-01-02']

In [5]:
from sklearn.preprocessing import MinMaxScaler
mms = MinMaxScaler()
df_subset[['z', 'pv', 'r', 'q', 't', 'u', 'vo', 'v', 
           'u10', 'v10', 't2m', 'tisr', 'tcc', 'tp', 
           'wind_speed', 'wind_dir']] = mms.fit_transform(df_subset[['z', 'pv', 'r', 'q', 
                                                                     't', 'u', 'vo', 'v', 
                                                                     'u10', 'v10', 't2m', 
                                                                     'tisr', 'tcc', 'tp', 
                                                                     'wind_speed', 'wind_dir']])

C:\Users\obsid\AppData\Local\Temp\ipykernel_33860\2820146458.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subset[['z', 'pv', 'r', 'q', 't', 'u', 'vo', 'v',


In [6]:
df_subset["lat"].unique()

array([-87.1875, -81.5625, -75.9375, -70.3125, -64.6875, -59.0625,
       -53.4375, -47.8125, -42.1875, -36.5625, -30.9375, -25.3125,
       -19.6875, -14.0625,  -8.4375,  -2.8125,   2.8125,   8.4375,
        14.0625,  19.6875,  25.3125,  30.9375,  36.5625,  42.1875,
        47.8125,  53.4375,  59.0625,  64.6875,  70.3125,  75.9375,
        81.5625,  87.1875])

In [7]:
df_subset["lon"].unique()

array([  0.   ,   5.625,  11.25 ,  16.875,  22.5  ,  28.125,  33.75 ,
        39.375,  45.   ,  50.625,  56.25 ,  61.875,  67.5  ,  73.125,
        78.75 ,  84.375,  90.   ,  95.625, 101.25 , 106.875, 112.5  ,
       118.125, 123.75 , 129.375, 135.   , 140.625, 146.25 , 151.875,
       157.5  , 163.125, 168.75 , 174.375, 180.   , 185.625, 191.25 ,
       196.875, 202.5  , 208.125, 213.75 , 219.375, 225.   , 230.625,
       236.25 , 241.875, 247.5  , 253.125, 258.75 , 264.375, 270.   ,
       275.625, 281.25 , 286.875, 292.5  , 298.125, 303.75 , 309.375,
       315.   , 320.625, 326.25 , 331.875, 337.5  , 343.125, 348.75 ,
       354.375])

In [8]:
df_subset["time"].unique()

array(['2018-01-01 00:00:00', '2018-01-01 01:00:00',
       '2018-01-01 02:00:00', '2018-01-01 03:00:00',
       '2018-01-01 04:00:00', '2018-01-01 05:00:00',
       '2018-01-01 06:00:00', '2018-01-01 07:00:00',
       '2018-01-01 08:00:00', '2018-01-01 09:00:00',
       '2018-01-01 10:00:00', '2018-01-01 11:00:00',
       '2018-01-01 12:00:00', '2018-01-01 13:00:00',
       '2018-01-01 14:00:00', '2018-01-01 15:00:00',
       '2018-01-01 16:00:00', '2018-01-01 17:00:00',
       '2018-01-01 18:00:00', '2018-01-01 19:00:00',
       '2018-01-01 20:00:00', '2018-01-01 21:00:00',
       '2018-01-01 22:00:00', '2018-01-01 23:00:00'], dtype=object)

In [ ]:
A_total = []
for N in (df_subset["time"].unique()):
    A = []
    for i in  (df_subset["lat"].unique()):
        matrix = []
        for j in  (df_subset["lon"].unique()):
            row = []
            for k in  (df_subset["level"].unique()[1:]):
                print("N: ", N, "i: ", i, "j: ", j, "k: ", k)
                row = row + [df_subset[(df_subset['time'] == N) &
                                       (df_subset['lat'] == i) & 
                                       (df_subset['lon'] == j) & 
                                       (df_subset['level'] == k)].drop(columns=["time","lat","lon","level"]).values[0]]
            matrix = matrix + [row]
        A = A + [matrix]
    A_total = A_total + [A]

N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  100
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  150
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  200
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  250
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  300
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  400
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  500
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  600
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  700
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  850
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  925
N:  2018-01-01 00:00:00 i:  -87.1875 j:  0.0 k:  1000
N:  2018-01-01 00:00:00 i:  -87.1875 j:  5.625 k:  100
N:  2018-01-01 00:00:00 i:  -87.1875 j:  5.625 k:  150
N:  2018-01-01 00:00:00 i:  -87.1875 j:  5.625 k:  200
N:  2018-01-01 00:00:00 i:  -87.1875 j:  5.625 k:  250
N:  2018-01-01 00:00:00 i:  -87.1875 j:  5.625 k:  300
N:  2018-01-01 00:00:00 i:  -87.1875 j:  5.625 k:  400
N:  2018-01-01 00:00:00 i:  -87.1

N:  2018-01-01 00:00:00 i:  -87.1875 j:  67.5 k:  400
N:  2018-01-01 00:00:00 i:  -87.1875 j:  67.5 k:  500
N:  2018-01-01 00:00:00 i:  -87.1875 j:  67.5 k:  600
N:  2018-01-01 00:00:00 i:  -87.1875 j:  67.5 k:  700
N:  2018-01-01 00:00:00 i:  -87.1875 j:  67.5 k:  850
N:  2018-01-01 00:00:00 i:  -87.1875 j:  67.5 k:  925
N:  2018-01-01 00:00:00 i:  -87.1875 j:  67.5 k:  1000
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  100
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  150
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  200
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  250
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  300
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  400
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  500
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  600
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  700
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  850
N:  2018-01-01 00:00:00 i:  -87.1875 j:  73.125 k:  925
N:  2

N:  2018-01-01 00:00:00 i:  -87.1875 j:  135.0 k:  1000
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  100
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  150
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  200
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  250
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  300
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  400
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  500
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  600
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  700
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  850
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  925
N:  2018-01-01 00:00:00 i:  -87.1875 j:  140.625 k:  1000
N:  2018-01-01 00:00:00 i:  -87.1875 j:  146.25 k:  100
N:  2018-01-01 00:00:00 i:  -87.1875 j:  146.25 k:  150
N:  2018-01-01 00:00:00 i:  -87.1875 j:  146.25 k:  200
N:  2018-01-01 00:00:00 i:  -87.1875 j:  146.25 k:  250
N:  2018-01-01 00:00:00 i:  -87.187

N:  2018-01-01 00:00:00 i:  -87.1875 j:  208.125 k:  400
N:  2018-01-01 00:00:00 i:  -87.1875 j:  208.125 k:  500
N:  2018-01-01 00:00:00 i:  -87.1875 j:  208.125 k:  600
N:  2018-01-01 00:00:00 i:  -87.1875 j:  208.125 k:  700
N:  2018-01-01 00:00:00 i:  -87.1875 j:  208.125 k:  850
N:  2018-01-01 00:00:00 i:  -87.1875 j:  208.125 k:  925
N:  2018-01-01 00:00:00 i:  -87.1875 j:  208.125 k:  1000
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  100
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  150
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  200
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  250
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  300
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  400
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  500
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  600
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  700
N:  2018-01-01 00:00:00 i:  -87.1875 j:  213.75 k:  850
N:  2018-01-01 00:00:00 i:  -87.1875 j: 

N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  100
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  150
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  200
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  250
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  300
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  400
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  500
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  600
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  700
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  850
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  925
N:  2018-01-01 00:00:00 i:  -87.1875 j:  281.25 k:  1000
N:  2018-01-01 00:00:00 i:  -87.1875 j:  286.875 k:  100
N:  2018-01-01 00:00:00 i:  -87.1875 j:  286.875 k:  150
N:  2018-01-01 00:00:00 i:  -87.1875 j:  286.875 k:  200
N:  2018-01-01 00:00:00 i:  -87.1875 j:  286.875 k:  250
N:  2018-01-01 00:00:00 i:  -87.1875 j:  286.875 k:  300
N:  2018-01-01 00:00:00 i:  -87.1875 j:  2

...

N:  2018-01-01 03:00:00 i:  -19.6875 j:  73.125 k:  300
N:  2018-01-01 03:00:00 i:  -19.6875 j:  73.125 k:  400
N:  2018-01-01 03:00:00 i:  -19.6875 j:  73.125 k:  500
N:  2018-01-01 03:00:00 i:  -19.6875 j:  73.125 k:  600
N:  2018-01-01 03:00:00 i:  -19.6875 j:  73.125 k:  700
N:  2018-01-01 03:00:00 i:  -19.6875 j:  73.125 k:  850
N:  2018-01-01 03:00:00 i:  -19.6875 j:  73.125 k:  925
N:  2018-01-01 03:00:00 i:  -19.6875 j:  73.125 k:  1000
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  100
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  150
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  200
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  250
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  300
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  400
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  500
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  600
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  700
N:  2018-01-01 03:00:00 i:  -19.6875 j:  78.75 k:  850
N

N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  100
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  150
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  200
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  250
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  300
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  400
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  500
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  600
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  700
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  850
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  925
N:  2018-01-01 03:00:00 i:  -19.6875 j:  146.25 k:  1000
N:  2018-01-01 03:00:00 i:  -19.6875 j:  151.875 k:  100
N:  2018-01-01 03:00:00 i:  -19.6875 j:  151.875 k:  150
N:  2018-01-01 03:00:00 i:  -19.6875 j:  151.875 k:  200
N:  2018-01-01 03:00:00 i:  -19.6875 j:  151.875 k:  250
N:  2018-01-01 03:00:00 i:  -19.6875 j:  151.875 k:  300
N:  2018-01-01 03:00:00 i:  -19.6875 j:  1

N:  2018-01-01 03:00:00 i:  -19.6875 j:  213.75 k:  500
N:  2018-01-01 03:00:00 i:  -19.6875 j:  213.75 k:  600
N:  2018-01-01 03:00:00 i:  -19.6875 j:  213.75 k:  700
N:  2018-01-01 03:00:00 i:  -19.6875 j:  213.75 k:  850
N:  2018-01-01 03:00:00 i:  -19.6875 j:  213.75 k:  925
N:  2018-01-01 03:00:00 i:  -19.6875 j:  213.75 k:  1000
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  100
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  150
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  200
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  250
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  300
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  400
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  500
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  600
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  700
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  850
N:  2018-01-01 03:00:00 i:  -19.6875 j:  219.375 k:  925
N:  2018-01-01 03:00:00 i:  -19.6875

N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  150
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  200
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  250
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  300
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  400
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  500
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  600
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  700
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  850
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  925
N:  2018-01-01 03:00:00 i:  -19.6875 j:  286.875 k:  1000
N:  2018-01-01 03:00:00 i:  -19.6875 j:  292.5 k:  100
N:  2018-01-01 03:00:00 i:  -19.6875 j:  292.5 k:  150
N:  2018-01-01 03:00:00 i:  -19.6875 j:  292.5 k:  200
N:  2018-01-01 03:00:00 i:  -19.6875 j:  292.5 k:  250
N:  2018-01-01 03:00:00 i:  -19.6875 j:  292.5 k:  300
N:  2018-01-01 03:00:00 i:  -19.6875 j:  292.5 k:  400
N:  2018-01-01 03:00:00 i:  -19.6875 j:  2

N:  2018-01-01 03:00:00 i:  -19.6875 j:  354.375 k:  300
N:  2018-01-01 03:00:00 i:  -19.6875 j:  354.375 k:  400
N:  2018-01-01 03:00:00 i:  -19.6875 j:  354.375 k:  500
N:  2018-01-01 03:00:00 i:  -19.6875 j:  354.375 k:  600
N:  2018-01-01 03:00:00 i:  -19.6875 j:  354.375 k:  700
N:  2018-01-01 03:00:00 i:  -19.6875 j:  354.375 k:  850
N:  2018-01-01 03:00:00 i:  -19.6875 j:  354.375 k:  925
N:  2018-01-01 03:00:00 i:  -19.6875 j:  354.375 k:  1000
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  100
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  150
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  200
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  250
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  300
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  400
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  500
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  600
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  700
N:  2018-01-01 03:00:00 i:  -14.0625 j:  0.0 k:  850
N:  2018-01-0

In [ ]:
np.save('reshaped_array', A_total)

In [ ]:
A_array = np.array(A_total)

In [ ]:
A_array.shape

In [16]:
input_layer = Input(shape=(32, 64, 12, 16), name="INPUT")
#x = data_augmentation(input_layer)
# Encoding
x = Conv3D(32, (2, 2, 2), activation='relu', padding='same')(input_layer)
x = MaxPooling3D((2, 2, 2))(x)
x = Conv3D(16, (2, 2, 2), activation='relu', padding='same')(x)
x = MaxPooling3D((2, 2, 2))(x)
x = Conv3D(16, (2, 2, 1), activation='relu', padding='same')(x)
x = MaxPooling3D((2, 2, 1))(x)

# Dense latent factors.
x = tf.keras.layers.Flatten()(x)
latent = tf.keras.layers.Dense(64)(x)
x = tf.keras.layers.Dense(4*8*3*16,activation='relu')(latent)
x = tf.keras.layers.Reshape((4,8,3,16))(x)

# Decoding
x = Conv3DTranspose(16, (2, 2, 1), activation='relu', padding='same')(x)
x = UpSampling3D((2, 2, 1))(x)
x = Conv3DTranspose(16, (2, 2, 2), activation='relu', padding='same')(x)
x = UpSampling3D((2, 2, 2))(x)
x = Conv3DTranspose(32, (2, 2, 2), activation='relu', padding='same')(x)
x = UpSampling3D((2,2, 2))(x)
output_layer = Conv3D(16, (2, 2, 2), padding='same', name="OUTPUT")(x)


autoencoder = Model(input_layer, output_layer)
autoencoder.compile(optimizer='adam', loss='mse')
autoencoder.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 INPUT (InputLayer)          [(None, 32, 64, 12, 16)]  0         
                                                                 
 conv3d (Conv3D)             (None, 32, 64, 12, 32)    4128      
                                                                 
 max_pooling3d (MaxPooling3D  (None, 16, 32, 6, 32)    0         
 )                                                               
                                                                 
 conv3d_1 (Conv3D)           (None, 16, 32, 6, 16)     4112      
                                                                 
 max_pooling3d_1 (MaxPooling  (None, 8, 16, 3, 16)     0         
 3D)                                                             
                                                                 
 conv3d_2 (Conv3D)           (None, 8, 16, 3, 16)      1040  

In [17]:
A_array.shape

(24, 32, 64, 12, 16)

In [18]:
autoencoder.fit(A_array, A_array, epochs=5, steps_per_epoch=10, batch_size=16)

Epoch 1/5
10/10 [==============================] - 7s 147ms/step - loss: 0.0783
Epoch 2/5
10/10 [==============================] - 2s 167ms/step - loss: 0.0783


In [ ]:
A_total = []
for N in (df.loc[(df["time"] >= '2018-01-02') & (df["time"] <= '2018-01-03')]["time"].unique()):
    A = []
    for i in  (df_subset["lat"].unique()):
        matrix = []
        for j in  (df_subset["lon"].unique()):
            row = []
            for k in  (df_subset["level"].unique()[1:]):
                row = row + [df_subset[(df_subset['lat'] == -87.1875) & 
                                       (df_subset['lon'] == 0) & 
                                       (df_subset['level'] == 1000)].drop(columns=["lat","lon","level"]).values[0]]
            matrix = matrix + [row]
        A = A + [matrix]
    A_total = A_total + [A]
pred_array = np.array(A_total)

In [ ]:
pred_array.shape